# Unbalanced data set

In [1]:
import pandas as pd
import numpy as np
import pickle

from tensorflow.keras.preprocessing.text import Tokenizer
import tensorflow as tf
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM,GRU
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Flatten,Activation, Dropout
from tensorflow.keras.layers import Conv1D, MaxPooling1D, GlobalMaxPooling1D 
from sklearn.model_selection import train_test_split

C:\Users\sathi\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\sathi\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\sathi\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\sathi\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:519: FutureWarning: Passi

In [2]:
from tqdm import tqdm
from nltk.tokenize import word_tokenize

In [3]:
#read pickle file
train=pd.read_pickle("train_second_data.pkl")
train

ID                                             Review  Rating  \
0          0  exceptional service nice daughter priced king ...       5   
1          1  beautiful relaxing jw marriott desert ridge ou...       5   
2          2  location location min subway take blommingdale...       5   
3          3  pleased nice safe flower market vast array res...       3   
4          4  excellent service excellent location couple mi...       4   
...      ...                                                ...     ...   
14338  14338  madrid perfect location tiny quiet street cent...       5   
14339  14339  excellent florence chosen tripadviser hidden g...       5   
14340  14340  place relax vacation book trip paradisus husba...       4   
14341  14341  week seattle loved minute pacific plaza buy im...       3   
14342  14342  clear internet reservation friday rang hour ad...       1   

       subjectivity  polarity Review_Type  
0          0.760000  0.427222    Positive  
1          0.837870  0.564907    Positive  
2          0.513333  0.273333    Positive  
3          0.613636  0.196970    Positive  
4          0.766667  0.654167    Positive  
...             ...       ...         ...  
14338      0.566667  0.333333    Positive  
14339      0.710417  0.403125    Positive  
14340      0.479297  0.209258    Positive  
14341      0.600000  0.433333    Positive  
14342      0.566667 -0.100000    Negative  

[14343 rows x 6 columns]

In [4]:
#read pickle file for test data
test_data=pd.read_pickle("test_df.pkl")
test_data

ID                                             Review
0        0  just superb rendezvous just perfect property s...
1        1  better close staten island ferry easy subway  ...
2        2  enjoyed stay  just come long weekend barcelona...
3        3  muse great  muse hotel great  did n t hear noi...
4        4  conveniently located morning flight  family st...
...    ...                                                ...
6143  6143  great hotel precruise great hotel arrived earl...
6144  6144  great choice just returned nights grand hotel ...
6145  6145  overpriced tiny rooms kowloon past use date ne...
6146  6146  ok  agree said positive staff helpful rooms cl...
6147  6147  great location husband stayed new orleans     ...

[6148 rows x 2 columns]

In [6]:
#based on polarity score create new rating columns
""""def getAnalysis(score):
    if score<0 and score> -1:
        return 1
    elif score>0 and score<.15 :
        return 2
    elif score>.15 and score<.25 :
        return 3
    elif score>.25 and score<.35 :
        return 4
    
    else:
        return 5"""

In [5]:
""""train["New_Rating"]=train["polarity"].apply(getAnalysis)
train"""

'"train["New_Rating"]=train["polarity"].apply(getAnalysis)\ntrain'

In [5]:
#create new data frame that contains only Reviews and New_Rating columns
train_data=train[["Review","Rating"]]
train_data

Review  Rating
0      exceptional service nice daughter priced king ...       5
1      beautiful relaxing jw marriott desert ridge ou...       5
2      location location min subway take blommingdale...       5
3      pleased nice safe flower market vast array res...       3
4      excellent service excellent location couple mi...       4
...                                                  ...     ...
14338  madrid perfect location tiny quiet street cent...       5
14339  excellent florence chosen tripadviser hidden g...       5
14340  place relax vacation book trip paradisus husba...       4
14341  week seattle loved minute pacific plaza buy im...       3
14342  clear internet reservation friday rang hour ad...       1

[14343 rows x 2 columns]

In [12]:
#create a a pickle file
with open("train_third_data.pkl", "wb") as picklefile:
         pickle.dump(train_data, picklefile)

# WORD EMBEDDING USING ONE HOT

In [6]:
text = train_data['Review'].tolist()
text[:10]

['exceptional service nice daughter priced king suite weekend night impressed exceptionally welcoming service reservation departure employee talked friendly eager question amazed age shaped pool tiny looked fun kid hot tub exercise breakfast abundant make waffle add scrambled egg bacon sausage fruit bagel muffin oatmeal yogurt wanted morning sort long line waiting make waffle waiting scrambled egg nice asked freeway reading review earlier bit noisy hey city felt deluxe reasonable price nice bedding art wall space needle bit window shuttle run hourly reserve place worked shuttle missed minute needed return space needle promptly paid cab fare asked downtown seattle',
 'beautiful relaxing jw marriott desert ridge outstanding accommodation business pleasure husband business conference march april enjoyed tremendously half hour drive airport beautiful impressive marble entry fountain balcony overlooked pool lazy river golf palm tree restaurant excellent service delicious food enjoyed merita

In [7]:
token = Tokenizer()
token.fit_on_texts(text)
token

In [8]:
#set vocabulary size
vocab_size = len(token.word_index) + 1
vocab_size

37223

In [14]:
#creare corpus for train data
corpuss = []
for i in range(0, len(train_data["Review"])):
    #print(i)
    review = train_data['Review'][i]
    review = review.lower()
    review = review.split()
    review = ' '.join(review)
    corpuss.append(review)

In [11]:
print(corpuss)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
onehot_repr=[one_hot(words,vocab_size)for words in corpuss] 
onehot_repr

[[11623,
  36620,
  22388,
  32037,
  28614,
  15043,
  27446,
  36117,
  7146,
  11756,
  21428,
  32140,
  36620,
  23575,
  17588,
  29237,
  5674,
  19710,
  10397,
  29416,
  29762,
  18425,
  17042,
  15665,
  13117,
  30729,
  35190,
  2982,
  36931,
  20108,
  23541,
  28449,
  6505,
  15911,
  6181,
  12797,
  1099,
  27202,
  7581,
  6290,
  28246,
  26458,
  23764,
  18082,
  18699,
  17269,
  25947,
  35531,
  7913,
  4752,
  13300,
  15911,
  6181,
  13300,
  1099,
  27202,
  22388,
  14297,
  28610,
  13804,
  17436,
  7560,
  10361,
  40,
  6084,
  15251,
  31524,
  9855,
  7204,
  19937,
  22388,
  16280,
  29611,
  11056,
  31293,
  15840,
  10361,
  25363,
  699,
  4349,
  17039,
  2596,
  33350,
  33024,
  699,
  22426,
  3796,
  37172,
  33048,
  31293,
  15840,
  22916,
  37214,
  29167,
  25396,
  14297,
  1547,
  19038],
 [17997,
  36615,
  6255,
  19222,
  25541,
  31597,
  17927,
  8075,
  24263,
  8454,
  13302,
  24263,
  10777,
  10596,
  9624,
  10260,
  29

In [11]:
#Embedding represenation
sent_length=100
X=pad_sequences(onehot_repr,padding='post',maxlen=sent_length)
#print(embedded_docs)

In [12]:
X

array([[11623, 36620, 22388, ..., 19038,     0,     0],
       [17997, 36615,  6255, ...,     0,     0,     0],
       [21308, 21308, 30692, ...,     0,     0,     0],
       ...,
       [17761, 37146, 28324, ...,  1614, 34140, 21308],
       [ 9435, 19038, 21455, ...,     0,     0,     0],
       [32144, 17112, 23575, ...,     0,     0,     0]])

In [13]:
#Get the Features

y=train_data["Rating"]
test=test_data["Review"]

In [14]:
X.shape

(14343, 100)

In [15]:
#aplitting the data
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 42, test_size = 0.2, stratify = y)

# MODEL BUILDING USING NEURAL NETWORKS

In [16]:
vect_size=300
model=Sequential()
model.add(Embedding(vocab_size,vect_size,input_length=sent_length))
#model.add(GRU(units=32,dropout=0.2,recurrent_dropout=0.2))



model.add(Conv1D(64, 8, activation = 'relu'))
model.add(MaxPooling1D(2))
model.add(Dropout(0.2))

model.add(Dense(30, activation='relu'))
model.add(Dropout(0.5))

model.add(Dense(30, activation='relu'))

model.add(GlobalMaxPooling1D())

model.add(Dense(6, activation='softmax'))

Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [17]:
model.compile(optimizer='adam', loss = 'sparse_categorical_crossentropy', metrics = ['accuracy'])

In [18]:
print(model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 100, 300)          11166900  
_________________________________________________________________
conv1d (Conv1D)              (None, 93, 64)            153664    
_________________________________________________________________
max_pooling1d (MaxPooling1D) (None, 46, 64)            0         
_________________________________________________________________
dropout (Dropout)            (None, 46, 64)            0         
_________________________________________________________________
dense (Dense)                (None, 46, 30)            1950      
_________________________________________________________________
dropout_1 (Dropout)          (None, 46, 30)            0         
_________________________________________________________________
dense_1 (Dense)              (None, 46, 30)            9

In [20]:
%%time
Embed_model=model.fit(X_train, y_train, epochs = 10, validation_split = 0.2,verbose=2,batch_size=128)

Train on 9179 samples, validate on 2295 samples
Epoch 1/10
9179/9179 - 26s - loss: 0.5889 - acc: 0.7581 - val_loss: 1.0712 - val_acc: 0.5468
Epoch 2/10
9179/9179 - 26s - loss: 0.4694 - acc: 0.8139 - val_loss: 1.1755 - val_acc: 0.5455
Epoch 3/10
9179/9179 - 26s - loss: 0.3880 - acc: 0.8500 - val_loss: 1.2704 - val_acc: 0.5198
Epoch 4/10
9179/9179 - 26s - loss: 0.3091 - acc: 0.8824 - val_loss: 1.3973 - val_acc: 0.5333
Epoch 5/10
9179/9179 - 26s - loss: 0.2512 - acc: 0.9055 - val_loss: 1.5781 - val_acc: 0.5237
Epoch 6/10
9179/9179 - 26s - loss: 0.1999 - acc: 0.9289 - val_loss: 1.7335 - val_acc: 0.5298
Epoch 7/10
9179/9179 - 26s - loss: 0.1605 - acc: 0.9431 - val_loss: 1.8356 - val_acc: 0.5203
Epoch 8/10
9179/9179 - 26s - loss: 0.1368 - acc: 0.9520 - val_loss: 2.0027 - val_acc: 0.5011
Epoch 9/10
9179/9179 - 26s - loss: 0.1286 - acc: 0.9552 - val_loss: 2.1312 - val_acc: 0.5098
Epoch 10/10
9179/9179 - 27s - loss: 0.1001 - acc: 0.9662 - val_loss: 2.2302 - val_acc: 0.5168
Wall time: 4min 19s


# preprocessing test data¶

In [21]:
test_data.head()

ID                                             Review
0   0  just superb rendezvous just perfect property s...
1   1  better close staten island ferry easy subway  ...
2   2  enjoyed stay  just come long weekend barcelona...
3   3  muse great  muse hotel great  did n t hear noi...
4   4  conveniently located morning flight  family st...

In [22]:
test = test_data["Review"].tolist()
test

['just superb rendezvous just perfect property singapore  fourth time family stayed property clean staff welcoming standards service second none  stayed york terrible westin stamford excellent pricey rendezvous stacks counts  just perfect location right  n t better return therendezvous   ',
 'better close staten island ferry easy subway  room fine comfortable clean  odd n t include tea coffee making facilities room  apparently free tea coffee lounge downstairs did n t manage  came room day door n t closed properly alarmed  security came eventually said housekeeping probably not pulled shut cleaning  guard said check records entered room later called details  records wrong housekeeping entered room morning left certainly n t case told times actually left entered heard matter look nothing taken probably innocent mistake guard bit nonchalant liking  good follow up issue overall ok stay loved bulgari toiletries not overly impressed   ',
 'enjoyed stay  just come long weekend barcelona stay

In [23]:
tokens = Tokenizer()
tokens.fit_on_texts(test)
tokens

In [24]:
#set vocabulary size
voc_size = len(tokens.word_index) + 1
voc_size

26615

In [25]:
#create corpus for test data
corpus = []
for i in range(0, len(test_data["Review"])):
    #print(i)
    review = test_data['Review'][i]
    review = review.lower()
    review = review.split()
    review = ' '.join(review)
    corpus.append(review)

In [26]:
#one hot representation
onehot_repr=[one_hot(words,vocab_size)for words in corpus] 
onehot_repr

[[32395,
  18741,
  28933,
  32395,
  14701,
  25184,
  14188,
  5572,
  32989,
  10086,
  14701,
  25184,
  1564,
  34769,
  32140,
  15749,
  36620,
  36631,
  14165,
  14701,
  28035,
  13414,
  35134,
  8498,
  12367,
  22754,
  28933,
  13229,
  3654,
  32395,
  14701,
  21308,
  360,
  19382,
  19003,
  35684,
  33048,
  8302],
 [35684,
  5500,
  27690,
  17775,
  30138,
  4615,
  9323,
  21950,
  20038,
  13758,
  1564,
  24699,
  19382,
  19003,
  16833,
  25672,
  13378,
  4594,
  4625,
  21950,
  16959,
  37032,
  25672,
  13378,
  19354,
  15320,
  10024,
  19382,
  19003,
  23616,
  7785,
  21950,
  10136,
  11059,
  19382,
  19003,
  6510,
  7431,
  17633,
  32507,
  7785,
  13287,
  24369,
  2791,
  16200,
  25298,
  34978,
  11206,
  25487,
  3440,
  24369,
  24103,
  30643,
  6009,
  21950,
  1400,
  34718,
  6030,
  30643,
  13548,
  2791,
  6009,
  21950,
  25947,
  2670,
  33782,
  19382,
  19003,
  9509,
  540,
  32851,
  12644,
  2670,
  6009,
  17791,
  6449,
  94

In [27]:
#Embedding represenation
sent_length=100
test_Emb_data=pad_sequences(onehot_repr,padding='post',maxlen=sent_length)
print(test_Emb_data)

[[32395 18741 28933 ...     0     0     0]
 [35684  5500 27690 ... 23542 11756     0]
 [12311 10228  5012 ... 34870 34960 11614]
 ...
 [10876 13117 32814 ...     0     0     0]
 [31771  5303 24369 ...     0     0     0]
 [25267 21308 13302 ...     0     0     0]]


In [28]:
test_Emb_data.shape

(6148, 100)

In [29]:
y_pred=model.predict(test_Emb_data)
y_pred

array([[2.1309099e-16, 2.4249443e-19, 6.5572213e-12, 2.5475298e-13,
        2.1765998e-04, 9.9978238e-01],
       [5.4492273e-09, 1.7152855e-07, 1.1260083e-02, 7.9378100e-05,
        8.9746165e-01, 9.1198675e-02],
       [7.3116568e-10, 7.2980300e-10, 2.5738939e-04, 5.8623327e-06,
        2.3745631e-01, 7.6228040e-01],
       ...,
       [1.3463360e-05, 2.3694986e-01, 7.5779641e-01, 4.2296043e-03,
        9.9078228e-04, 1.9810081e-05],
       [2.0375087e-07, 7.3207218e-09, 3.3832330e-05, 1.6048081e-03,
        7.3498112e-01, 2.6337999e-01],
       [4.4442900e-06, 4.4576038e-05, 1.1380075e-02, 5.0073426e-02,
        7.9844832e-01, 1.4004913e-01]], dtype=float32)

In [30]:
y_pred = np.argmax(y_pred, axis=1)


In [31]:
y_pred

array([5, 4, 5, ..., 2, 4, 4], dtype=int64)

In [32]:
y_test_labels = np.argmax(test_Emb_data, axis =1)
y_test_labels

array([17, 85, 29, ...,  8,  3, 44], dtype=int64)

In [169]:
y_train_labels=y_train

# How to improve the performance?

Re-sampling Dataset

To make our dataset balanced there are two ways to do so:

Under-sampling: Remove samples from over-represented classes ; use this if you have huge dataset

Over-sampling: Add more samples from under-represented classes; use this if you have small dataset

Over-sampling: SMOTE

SMOTE (Synthetic Minority Oversampling TEchnique) consists of synthesizing elements for the minority class, 
based on those that already exist. It works randomly picking a point from the minority class and computing 
the k-nearest neighbors for this point.The synthetic points are added between the chosen point and its neighbors.
We'll use ratio='minority' to resample the minority class.

In [162]:
from imblearn.over_sampling import SMOTE
smote = SMOTE('minority')

X_sm, y_sm = smote.fit_sample(X_train, y_train)
print(X_sm.shape, y_sm.shape)

(15841, 200) (15841,)


In [173]:
from sklearn.utils import class_weight
class_weight = class_weight.compute_class_weight('balanced' ,np.unique(y_train_labels) ,y_train_labels)

In [174]:
model.fit(X_sm, y_sm, epochs = 10, validation_split = 0.2,verbose=2,batch_size=128,class_weight=class_weight)

Train on 12672 samples, validate on 3169 samples
Epoch 1/10
12672/12672 - 55s - loss: 0.6009 - acc: 0.7924 - val_loss: 0.2691 - val_acc: 0.9776
Epoch 2/10
12672/12672 - 58s - loss: 0.3737 - acc: 0.8617 - val_loss: 0.2520 - val_acc: 0.9568
Epoch 3/10
12672/12672 - 58s - loss: 0.2835 - acc: 0.8976 - val_loss: 0.2716 - val_acc: 0.9262
Epoch 4/10
12672/12672 - 57s - loss: 0.2285 - acc: 0.9162 - val_loss: 0.3088 - val_acc: 0.9015
Epoch 5/10
12672/12672 - 59s - loss: 0.1893 - acc: 0.9303 - val_loss: 0.5266 - val_acc: 0.8081
Epoch 6/10
12672/12672 - 57s - loss: 0.1456 - acc: 0.9479 - val_loss: 0.5658 - val_acc: 0.8034
Epoch 7/10
12672/12672 - 57s - loss: 0.1298 - acc: 0.9537 - val_loss: 0.6372 - val_acc: 0.7955
Epoch 8/10
12672/12672 - 57s - loss: 0.1240 - acc: 0.9565 - val_loss: 0.7906 - val_acc: 0.7438
Epoch 9/10
12672/12672 - 57s - loss: 0.0983 - acc: 0.9650 - val_loss: 0.8399 - val_acc: 0.7558
Epoch 10/10
12672/12672 - 59s - loss: 0.0926 - acc: 0.9691 - val_loss: 1.0051 - val_acc: 0.7109


In [176]:
score, acc = model.evaluate(X_test, y_test,
                       batch_size=128, verbose=2)

print('Test accuracy:', acc)

2869/2869 - 2s - loss: 2.4674 - acc: 0.4793
Test accuracy: 0.47926107


In [177]:
#Aplly test data and make pediction
y_pred=model.predict(test_Emb_data)
y_pred

array([[2.5283964e-09, 7.0183787e-06, 3.0265546e-06, 8.9390114e-06,
        5.3932879e-04, 9.9944168e-01],
       [2.6534592e-09, 1.4149240e-04, 5.1697195e-01, 4.8099253e-01,
        1.8939546e-03, 4.5250669e-08],
       [1.5002962e-11, 5.3729171e-05, 5.3470117e-01, 4.6450415e-01,
        7.4087724e-04, 6.6124848e-08],
       ...,
       [2.2325509e-11, 6.4163673e-01, 3.5795492e-01, 4.0831006e-04,
        1.0512295e-09, 6.4938362e-08],
       [2.0095054e-03, 1.3053144e-02, 5.4011371e-02, 1.0759555e-01,
        5.5945665e-01, 2.6387376e-01],
       [1.8486702e-05, 7.0637554e-02, 7.0215881e-02, 3.0190902e-02,
        8.7224469e-03, 8.2021469e-01]], dtype=float32)

In [178]:
y_pred = np.argmax(y_pred, axis=1)
y_pred

array([5, 2, 2, ..., 1, 4, 5], dtype=int64)

# using LSTM

# original data

In [23]:
vect_size=300
model=Sequential()
model.add(Embedding(vocab_size,vect_size,input_length=sent_length))
model.add(LSTM(100))
model.add(Dropout(0.2))

model.add(Dense(30, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(30, activation='relu'))
model.add(Dense(6, activation='softmax'))

Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [24]:
model.compile(optimizer='adam', loss = 'sparse_categorical_crossentropy', metrics = ['accuracy'])

In [25]:
model.fit(X_train, y_train, epochs = 10, validation_split = 0.2,verbose=2,batch_size=128)

Train on 9179 samples, validate on 2295 samples
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Epoch 1/10
9179/9179 - 86s - loss: 1.4986 - acc: 0.4259 - val_loss: 1.3811 - val_acc: 0.4549
Epoch 2/10
9179/9179 - 88s - loss: 1.3923 - acc: 0.4398 - val_loss: 1.3800 - val_acc: 0.4553
Epoch 3/10
9179/9179 - 90s - loss: 1.3763 - acc: 0.4463 - val_loss: 1.3592 - val_acc: 0.4553
Epoch 4/10
9179/9179 - 89s - loss: 1.3665 - acc: 0.4461 - val_loss: 1.3596 - val_acc: 0.4562
Epoch 5/10
9179/9179 - 91s - loss: 1.3611 - acc: 0.4447 - val_loss: 1.3347 - val_acc: 0.4562
Epoch 6/10
9179/9179 - 90s - loss: 1.3340 - acc: 0.4462 - val_loss: 1.3401 - val_acc: 0.4575
Epoch 7/10
9179/9179 - 89s - loss: 1.3306 - acc: 0.4442 - val_loss: 1.3186 - val_acc: 0.4553
Epoch 8/10
9179/9179 - 90s - loss: 1.3260 - acc: 0.4446 - val_loss: 1.3177 - val_acc: 0.4523
Epoch 9/10
9179/9179 - 91s - loss: 1.3214 - acc: 0.4474 - val_loss: 1.3237 - val_acc: 0.4505
Epoch 10/10
9179/9179

In [26]:
score, acc = model.evaluate(X_test, y_test,
                       batch_size=128, verbose=2)

print('Test accuracy:', acc)

2869/2869 - 5s - loss: 1.3431 - acc: 0.4211
Test accuracy: 0.42105263


# LSTM-sampled data

In [183]:
vect_size=300
model=Sequential()
model.add(Embedding(vocab_size,vect_size,input_length=sent_length))
model.add(LSTM(100))
model.add(Dropout(0.2))

model.add(Dense(30, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(30, activation='relu'))
model.add(Dense(6, activation='softmax'))

In [184]:
model.compile(optimizer='adam', loss = 'sparse_categorical_crossentropy', metrics = ['accuracy'])

In [ ]:
model.fit(X_sm, y_sm, epochs = 10, validation_split = 0.2,verbose=2,batch_size=128,class_weight=class_weight)

Train on 12672 samples, validate on 3169 samples
Epoch 1/10
12672/12672 - 151s - loss: 1.5246 - acc: 0.3845 - val_loss: 1.6732 - val_acc: 0.0000e+00
Epoch 2/10
12672/12672 - 162s - loss: 1.4563 - acc: 0.4037 - val_loss: 1.7187 - val_acc: 0.0000e+00
Epoch 3/10
12672/12672 - 156s - loss: 1.4408 - acc: 0.4054 - val_loss: 1.8612 - val_acc: 0.0000e+00
Epoch 4/10
12672/12672 - 153s - loss: 1.4312 - acc: 0.4108 - val_loss: 1.3261 - val_acc: 0.0044
Epoch 5/10
12672/12672 - 153s - loss: 1.4473 - acc: 0.3979 - val_loss: 1.7642 - val_acc: 3.1556e-04
Epoch 6/10
12672/12672 - 150s - loss: 1.4154 - acc: 0.4135 - val_loss: 1.7378 - val_acc: 0.0246
Epoch 7/10


# GLOVE embedding

In [16]:
train_data=pd.read_pickle("train_third_data.pkl")
train_data

Review  New_Rating
0      exceptional service nice daughter priced king ...           5
1      beautiful relaxing jw marriott desert ridge ou...           5
2      location location min subway take blommingdale...           4
3      pleased nice safe flower market vast array res...           3
4      excellent service excellent location couple mi...           5
...                                                  ...         ...
14338  madrid perfect location tiny quiet street cent...           4
14339  excellent florence chosen tripadviser hidden g...           5
14340  place relax vacation book trip paradisus husba...           3
14341  week seattle loved minute pacific plaza buy im...           5
14342  clear internet reservation friday rang hour ad...           1

[14343 rows x 2 columns]

In [17]:
test_data.head()

ID                                             Review
0   0  just superb rendezvous just perfect property s...
1   1  better close staten island ferry easy subway  ...
2   2  enjoyed stay  just come long weekend barcelona...
3   3  muse great  muse hotel great  did n t hear noi...
4   4  conveniently located morning flight  family st...

In [9]:
df=pd.concat([train_data,test_data])
df.shape

(20491, 3)

In [10]:
stop=pd.read_pickle("stp_wrds.pkl")

In [11]:
#glove vectorization
def create_corpus(df):
    corpus=[]
    for text in tqdm(df['Review']):
        words=[word.lower() for word in word_tokenize(text) if((word.isalpha()==1) & (word not in stop))]
        corpus.append(words)
    return corpus

In [12]:
corpus=create_corpus(df)

100%|██████████| 20491/20491 [00:33<00:00, 606.25it/s]


In [13]:
embedding_dict={}
with open('glove.6B.100d.txt','rb') as f:
    for line in f:
        values=line.split()
        word=values[0]
        vectors=np.asarray(values[1:],'float32')
        embedding_dict[word]=vectors
f.close()

In [14]:
MAX_LEN=150
tokenizer_obj=Tokenizer()
tokenizer_obj.fit_on_texts(corpus)
sequences=tokenizer_obj.texts_to_sequences(corpus)

review_pad=pad_sequences(sequences,maxlen=MAX_LEN,truncating='post',padding='post')

In [15]:
word_index=tokenizer_obj.word_index
print('Number of unique words:',len(word_index))

Number of unique words: 47375


In [16]:
num_words=len(word_index)+1
embedding_matrix=np.zeros((num_words,100))

for word,i in tqdm(word_index.items()):
    if i > num_words:
        continue
    
    emb_vec=embedding_dict.get(word)
    if emb_vec is not None:
        embedding_matrix[i]=emb_vec

100%|██████████| 47375/47375 [00:00<00:00, 669045.42it/s]


In [17]:
from keras.initializers import Constant
from keras.layers import SpatialDropout1D
from keras.optimizers import Adam

Using TensorFlow backend.


In [18]:
glove_model=Sequential()

embedding=Embedding(num_words,100,embeddings_initializer=Constant(embedding_matrix),
                   input_length=MAX_LEN,trainable=False)

glove_model.add(embedding)
glove_model.add(Dropout(0.5))
glove_model.add(LSTM(64, dropout=0.2, recurrent_dropout=0.2))
glove_model.add(Dense(6, activation='softmax'))




Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [19]:
optimzer=Adam(learning_rate=1e-5)

glove_model.compile(loss='sparse_categorical_crossentropy',optimizer=optimzer,metrics=['accuracy'])

In [20]:
train=review_pad[:train_data.shape[0]]
test=review_pad[train_data.shape[0]:]

In [21]:
X_train,X_test,y_train,y_test=train_test_split(train,train_data['Rating'].values,test_size=0.15)
print('Shape of train',X_train.shape)
print("Shape of Validation ",X_test.shape)

Shape of train (12191, 150)
Shape of Validation  (2152, 150)


In [22]:
history=glove_model.fit(X_train,y_train,batch_size=4,epochs=10,validation_data=(X_test,y_test),verbose=2)

Train on 12191 samples, validate on 2152 samples
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Epoch 1/10
12191/12191 - 307s - loss: 1.5364 - acc: 0.4502 - val_loss: 1.3866 - val_acc: 0.4391
Epoch 2/10
12191/12191 - 304s - loss: 1.3789 - acc: 0.4504 - val_loss: 1.3653 - val_acc: 0.4391
Epoch 3/10
12191/12191 - 303s - loss: 1.3623 - acc: 0.4504 - val_loss: 1.3598 - val_acc: 0.4391
Epoch 4/10
12191/12191 - 319s - loss: 1.3565 - acc: 0.4504 - val_loss: 1.3588 - val_acc: 0.4391
Epoch 5/10
12191/12191 - 308s - loss: 1.3558 - acc: 0.4504 - val_loss: 1.3573 - val_acc: 0.4391
Epoch 6/10
12191/12191 - 301s - loss: 1.3534 - acc: 0.4504 - val_loss: 1.3567 - val_acc: 0.4391
Epoch 7/10
12191/12191 - 304s - loss: 1.3528 - acc: 0.4504 - val_loss: 1.3565 - val_acc: 0.4391
Epoch 8/10
12191/12191 - 306s - loss: 1.3525 - acc: 0.4504 - val_loss: 1.3562 - val_acc: 0.4391
Epoch 9/10
12191/12191 - 303s - loss: 1.3528 - acc: 0.4504 - val_loss: 1.3563 - val_acc: 

In [23]:
score, acc = glove_model.evaluate(X_test, y_test,
                       batch_size=128, verbose=2)

print('Test accuracy:', acc)

2152/2152 - 1s - loss: 1.3563 - acc: 0.4391
Test accuracy: 0.4391264


In [ ]:
import torch

from simpletransformers.classification import ClassificationModel
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold

In [33]:
#upload sample submission file
sample_df=pd.read_csv("sample submission (2).csv")
sample_df

ID  Rating
0        0       5
1        1       1
2        2       4
3        3       4
4        4       4
...    ...     ...
6143  6143       5
6144  6144       4
6145  6145       3
6146  6146       4
6147  6147       4

[6148 rows x 2 columns]

In [34]:
#adding predicted Item_Outlet_Sales in to sample_df
pred=pd.DataFrame(y_pred)
data=pd.concat([sample_df["ID"],pred],axis=1)

data.columns=["ID","Rating"]
data.to_csv("sample submission (2).csv",index=False)